In [12]:
import pandas as pd
import datetime
import numpy as np
import re

In [1]:
placeNum = str(786)  
rawdata_picklePath = "../code/data/"+placeNum+"/"+placeNum+".p"

In [95]:
df = pd.read_pickle(rawdata_picklePath)

In [96]:
df

area  deny                         device_id  dwell_time  \
0             out   NaN  79c83d4e78dc4a82dd59f3e749163fb0           0   
1             out   NaN  eb1ac0bc6a77e7489441b476199f61c0         252   
2             out   NaN  f12cf7022c50eff86eb48301a3413dd1           0   
3             out   NaN  443d54b156d97f485ed5d3d3f29aaf95          16   
4             out   NaN  7a167cfafc749069f23fa1ba8341b639          29   
5             out   NaN  823b4c7e6e229bda7c8bc27f68a8e389          22   
6             out   NaN  6a24986e58546efd8c8f2b0386a30212          18   
7             out   NaN  11b0e560579b48ba189a828fc296b279          31   
8             out   NaN  64e998aa4845d055364a2d86a2571d62          29   
9             out   NaN  1b3536b0303eae6291ba9832414e1be8          20   
10            out  True  fbfea8a9b5472760d572422ce88bb319        1532   
11            out   NaN  9a7613b070f1cc50cb924ffc8f5ba6ed           0   
12            out   NaN  b546a6e16394d0ae5626be739e087296         121   
13            out   NaN  c8e20001131f8f0fc2f97108d3047514          10   
14            out   NaN  38b238906dd097f4291f60f4c8bbb886           0   
15            out   NaN  82b07f7e93ccc6d182c3ab9c0af3c7fb         417   
16            out   NaN  ba99e59073e37b5180c0270e80fbea5d           0   
17            out   NaN  8beacd77c80057861025e13793741584          70   
18            out   NaN  b1c0728948f10521695b9ff58c918e40           0   
19            out   NaN  5f946506583ffb5b6b7aa697eea25b21           9   
20            out   NaN  3b747298166d0a362f34135c2d593e97           0   
21            out   NaN  9726013d693dc0e8112d2e5d5bcf10d8           0   
22            out   NaN  e9e16f71e1e53a2f951bcecc07747924        1325   
23            out   NaN  538223c1d33c00bbaa726227c0f0232c           3   
24            out   NaN  9689f9d86d19e2a6106dd58f5ddb9beb           0   
25            out   NaN  5f736ac4f0e59be480484de48e8d8fb3           0   
26            out   NaN  23ebd787135b130b39dd800c8da66e38          18   
27            out   NaN  9afa8a88d2c46835bf737757fcae99c6           0   
28            out   NaN  6caabf8c096576eb907f6a79fa6c1a3c           0   
29            out   NaN  40103059d020119ffbd3e2a8d19a7eb4           0   
...           ...   ...                               ...         ...   
4551003       out   NaN  79973d410bf60f10b0e23d88fb5a65a2           4   
4551004       out   NaN  953811f9bd8223e6f35905be86e37012           0   
4551005       out   NaN  b4d3498eeb12fbdf4d3a5ef0a47445a6           5   
4551006       out   NaN  842e0a1aae59e8fd4a4bce865b389524           0   
4551007       out   NaN  9442d900a14b3682a7eeff01dffb4786        1055   
4551008       out   NaN  4961fa00a245ae52954dedbcf8c68f45        3270   
4551009       out   NaN  028a1f4dbca00ed06814fdda60f1b599        3548   
4551010       out   NaN  fa1f5d08eba95839db76ecbb97619c0b       48776   
4551011       out   NaN  84634b694d34053594bfd5fcbb2b5220          17   
4551012       out   NaN  3a45b9cb885ee694c6c0b2a96a87468f       48815   
4551013       out   NaN  d8d837f07fa661baafae573324c45b96          50   
4551014       out   NaN  f0652d4665d8f00c35a3b01a7699a6ce          16   
4551015       out   NaN  ca112676b76f0fe90ddee740b0459a97       48652   
4551016       out   NaN  54dfd78bf25c32eb0e5a3cd1bc9460bd       37916   
4551017       out  True  ec588edbcb0b6975125e3c441a389381       35156   
4551018       out   NaN  a6b7b09b93de015cd27da23cbd6c093c        3400   
4551019       out  True  1bb57295fdd527202a1aeac3e29b9504       24386   
4551020        1f  True  47cbc1c26d0aa075de241967ac014e51        3433   
4551021        in  True  47cbc1c26d0aa075de241967ac014e51        3433   
4551022       out  True  47cbc1c26d0aa075de241967ac014e51       48403   
4551023       out  True  678811f2ba54a0ab8b1738e61bcf6ea1        7230   
4551024  1f-inner  True  3cb3c5d41981dcf7f75ffc1db3378c6e       37968   
4551025       out   NaN  c9866cd15a94b493feb0c2816826bc8d        3971  

In [97]:
def finddata(logs, df, data):   # x is a list of logs
   return df.ix[logs][data].tolist()

def calend(x, y):
    print(x)
    print(y)
    return list(map(lambda i, j: i+j, x, y ))

def printall(mp, i, columnss):
    for column in columnss:
        print(mp[column].ix[i])

def reindex_by_moving_pattern(df):
    ### read data and reindex by date and device_id
    df.loc[:, 'date'] = df['ts'] // 86400000
    # df = df.loc[(df['dwell_time'] > 0)]
    df.loc[:, 'date_device_id'] = df.date.map(str) + "_" + df.device_id

    ### collect valid trajectories (ex. trajecties containing only 'out' area, such as 'out-out-out-out' are deleted)
    traj = df.groupby(['date_device_id'])['area']
    ar = ['out']
    temp = traj.unique()
    temp2 = temp[-temp.apply(lambda x: (x == ar).all())]
    print('Ratio of valid trajectory having not only \'out\' area: ', len(temp2)/len(temp))
    df2 = df[df.date_device_id.isin(temp2.index.tolist())]
   

    ### erase other useless trajectories having 'in' shorter than 100 seconds
    dfin = df2[df2['area'] == 'in']
    time = dfin.groupby(['date_device_id'])['dwell_time'].sum()
    time2 = time[time > 100]
    print('Ratio of trajectory staying \'in\' longer than 0 seconds: ', len(time2)/len(time))
    df3 = df2[df2.date_device_id.isin(time2.index.tolist())]
    
    del df, df2
    
    ### make a list of logs for corresponding each indoor moving trajectories 
    mplogs = df3.sort_index(ascending=False).groupby('date_device_id', sort=False).apply(lambda x: x.index.tolist()).sort_index()
    mpframe = mplogs.to_frame(name='logs').reset_index()
    
    
    mpframe.loc[:, 'traj'] = mpframe['logs'].apply(lambda x: finddata(x, df3, 'area'))
    mpframe.loc[:, 'ts'] = mpframe['logs'].apply(lambda x: finddata(x, df3, 'ts'))
    mpframe.loc[:, 'dwell_time'] = mpframe['logs'].apply(lambda x: finddata(x, df3, 'dwell_time'))
    mpframe.loc[:, 'ts'] = mpframe['ts'].apply(lambda x: [int(y/1000) for y in x])
    mpframe.loc[:, 'hour_start'] = mpframe['ts'].apply(lambda x: [int(datetime.datetime.fromtimestamp(y).strftime('%H')) for y in x])
    mpframe.loc[:, 'time_start'] = mpframe['ts'].apply(lambda x: [datetime.datetime.fromtimestamp(y).strftime('%H:%M:%S') for y in x])  # %Y-%m-%d 
    mpframe.loc[:, 'ts_end'] = mpframe[['ts', 'dwell_time']].apply(lambda x: calend(*x), axis=1)
    mpframe.loc[:, 'hour_end'] = mpframe['ts_end'].apply(lambda x: [int(datetime.datetime.fromtimestamp(y).strftime('%H')) for y in x])
    mpframe.loc[:, 'time_end'] = mpframe['ts_end'].apply(lambda x: [datetime.datetime.fromtimestamp(y).strftime('%H:%M:%S') for y in x])
    
    del df3
    return mpframe

In [98]:
df2 = reindex_by_moving_pattern(df)

Ratio of valid trajectory having not only 'out' area:  0.03276281190995878
Ratio of trajectory staying 'in' longer than 0 seconds:  0.23268507661828328
[1440750511, 1440751250, 1440751250, 1440751260, 1440751302, 1440751302, 1440751321, 1440751368]
[857, 118, 118, 108, 20, 28, 8, 0]
[1440725175, 1440726721, 1440727017, 1440727028, 1440727215, 1440727465, 1440727625, 1440727687, 1440727743, 1440727950]
[3548, 1293, 552, 418, 18, 6, 389, 266, 230, 14]
[1440753481, 1440753683, 1440753683, 1440753683, 1440754065]
[986, 565, 0, 565, 73]
[1440725586, 1440726737, 1440726743, 1440727780, 1440727780, 1440728239, 1440731397]
[2957, 168, 41, 459, 459, 0, 16]
[1440739692, 1440740611, 1440741689, 1440741689, 1440741709, 1440741720, 1440741754, 1440742874]
[0, 1528, 393, 393, 0, 30, 328, 0]
[1440755984, 1440755985, 1440755985, 1440756200, 1440756261, 1440756453]
[490, 468, 468, 252, 144, 0]
[1440742633, 1440742700, 1440742700, 1440743822, 1440748394, 1440754292, 1440759965, 1440759965]
[91, 0, 0, 23

In [101]:
def add_revisitcount(mpframe2, revisit_interval_thres):
    mpframe2['device_id'] = mpframe2['date_device_id'].apply(lambda x: x[6:])
    mpframe2['date'] = mpframe2['date_device_id'].apply(lambda x: int(x[:5]))
    mpframe2['cnt'] = 1
    mpframe2['new_visit_count'] = mpframe2[['device_id', 'cnt']].groupby('device_id').cumsum()
    mpframe2['revisit_intention'] = 0

    for ids in mpframe2['device_id'].unique():
        dff = mpframe2.loc[mpframe2['device_id']==ids]   
        a = 0
        date = min(dff.date)
        prev_idx = ''
        for index, row in dff.iterrows():
            if a+1 == row['new_visit_count']:
                if date+revisit_interval_thres > row['date']:
    ### DEBUG(print variables)
    #                 print('regular revisit: {0} days interval'.format(row['date']-date))
    #                 print('previous index: ',prev_idx)
                    mpframe2.set_value(prev_idx, 'revisit_intention', 1)
    #             elif row['new_visit_count'] == 1:
    #                 print('regular revisit: {0} days interval'.format(row['date']-date))
    #             else:
    #                 print('Irregular revisit: {0} days interval'.format(row['date']-date))
                prev_idx = index
    #             print(row,'\n')
                a = row['new_visit_count']
                date = row['date']

    del mpframe2['cnt']
    return mpframe2.ix[:-1]

In [102]:
df2sample = df2.head(5000)
df3sample = add_revisitcount(df2sample, 90)

/Users/sundong/anaconda/envs/py35/lib/python3.5/site-packages/ipykernel/__main__.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  from ipykernel import kernelapp as app
/Users/sundong/anaconda/envs/py35/lib/python3.5/site-packages/ipykernel/__main__.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  app.launch_new_instance()
/Users/sundong/anaconda/envs/py35/lib/python3.5/site-packages/ipykernel/__main__.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_index

In [108]:

limit_date = max(df3sample.date) - 90
recent3monthvisitors = df3sample.loc[(df3sample.date > limit_date)].index  ## & (df3sample.revisit_intention == 0)
df3sample_excludelast3months = df3sample.drop(recent3monthvisitors)

print(df3sample.shape)
print(df3sample_excludelast3months.shape)

(5000, 14)
(45, 14)


In [112]:
df3sample.revisit_intention.value_counts()


0.0    3576
1.0    1424
Name: revisit_intention, dtype: int64

In [125]:
from sklearn.model_selection import StratifiedKFold
from imblearn.over_sampling import RandomOverSampler

In [123]:
df3sample.revisit_intention.value_counts()

0.0    3576
1.0    1424
Name: revisit_intention, dtype: int64

In [126]:
ros = RandomOverSampler(random_state=42)
X_res, y_res = ros.fit_sample(df3sample, df3sample['revisit_intention'])

ValueError: could not convert string to float: '9f2d75c15ba4a9d9adbf3cf70dba5ad8'

In [118]:


skf = StratifiedKFold(n_splits=10)

for train_index, test_index in skf.split(df3sample, df3sample['revisit_intention']):
    df3sample_train = df3sample.ix[train_index]
    df3sample_test = df3sample.ix[test_index]
    print(df3sample_train.revisit_intention.value_counts())
    print(df3sample_test.revisit_intention.value_counts())

0.0    3218
1.0    1281
Name: revisit_intention, dtype: int64
0.0    358
1.0    143
Name: revisit_intention, dtype: int64
0.0    3218
1.0    1281
Name: revisit_intention, dtype: int64
0.0    358
1.0    143
Name: revisit_intention, dtype: int64
0.0    3218
1.0    1281
Name: revisit_intention, dtype: int64
0.0    358
1.0    143
Name: revisit_intention, dtype: int64
0.0    3218
1.0    1281
Name: revisit_intention, dtype: int64
0.0    358
1.0    143
Name: revisit_intention, dtype: int64
0.0    3218
1.0    1282
Name: revisit_intention, dtype: int64
0.0    358
1.0    142
Name: revisit_intention, dtype: int64
0.0    3218
1.0    1282
Name: revisit_intention, dtype: int64
0.0    358
1.0    142
Name: revisit_intention, dtype: int64
0.0    3219
1.0    1282
Name: revisit_intention, dtype: int64
0.0    357
1.0    142
Name: revisit_intention, dtype: int64
0.0    3219
1.0    1282
Name: revisit_intention, dtype: int64
0.0    357
1.0    142
Name: revisit_intention, dtype: int64
0.0    3219
1.0    1282


In [129]:
revisitintentionadded_picklePath = "../code/data/"+placeNum+"/"+placeNum+"_3_revisitintentionadded.p"
frequentvisitorremoved_picklePath = "../code/data/"+placeNum+"/"+placeNum+"_4_frequentvisitorremoved.p"
statistical_picklePath = "../code/data/"+placeNum+"/"+placeNum+"_5_statistical.p"

In [136]:
dff = pd.read_pickle(revisitintentionadded_picklePath)
dff.set_index('date_device_id')

logs  \
date_device_id                                                                              
16675_02614c7588f7f8eaa0d3b9047ac08410  [4545933, 4545741, 4545737, 4545720, 4545716, ...   
16675_028a1f4dbca00ed06814fdda60f1b599  [4551009, 4550832, 4550777, 4550731, 4550674, ...   
16675_062c73a8b307fd05f6af2472a35671ef               [4545181, 4545105, 4545104, 4544999]   
16675_06c041f68ec481883941d47d99d6903f  [4550980, 4550828, 4550826, 4550622, 4550540, ...   
16675_1257118518717340418bd1c3fc238246  [4548352, 4548153, 4547900, 4547896, 4547895, ...   
16675_15f34560566d4e2a05557426a36fe4f7      [4544488, 4544486, 4544433, 4544419, 4544380]   
16675_1b74f8c859dfb1d990a695ac8cb3d05a  [4547738, 4547722, 4547721, 4547529, 4546461, ...   
16675_1bb57295fdd527202a1aeac3e29b9504  [4551019, 4550979, 4550922, 4550608, 4550274, ...   
16675_2404cf1917d697fa384e1a9755a9b03c  [4549449, 4549372, 4548501, 4548500, 4543694, ...   
16675_26f20a4ede993ca25b0a558564d4519f                        [4543149, 4543148, 4543081]   
16675_29995dd65c3590dd0373029d2b10aaa8      [4546824, 4546342, 4546285, 4546284, 4546121]   
16675_31d9f57379338f49d1b11ecae74bb157      [4548932, 4548931, 4548930, 4548867, 4548719]   
16675_342a4950ee5d3de5ce96f27700a01297  [4550898, 4550897, 4550566, 4550565, 4550564, ...   
16675_3a256162262ef2f26d547642036db82b  [4551032, 4551031, 4550861, 4550860, 4550785, ...   
16675_3a45b9cb885ee694c6c0b2a96a87468f  [4551012, 4550775, 4550184, 4548861, 4548635, ...   
16675_3cb3c5d41981dcf7f75ffc1db3378c6e  [4551029, 4551028, 4551024, 4550947, 4550942, ...   
16675_3ffc4f8e98b3b07e5c6f1feae1820979  [4550936, 4550863, 4550862, 4550651, 4550649, ...   
16675_415f8975e9d94657b1ae518a5fdae9bd  [4550804, 4549158, 4548946, 4548943, 4548939, ...   
16675_47254b16635711f6b0efb88a82290e37  [4549969, 4549968, 4549957, 4549955, 4549009, ...   
16675_47cbc1c26d0aa075de241967ac014e51  [4551022, 4551021, 4550935, 4550744, 4550328, ...   
16675_4961fa00a245ae52954dedbcf8c68f45      [4551008, 4550691, 4550684, 4550594, 4549976]   
16675_49880202c685a316d11e321ef4cf98e0      [4548258, 4548172, 4548166, 4548165, 4548059]   
16675_4b9d47f55c0d1451f036850619d71ca3               [4548479, 4548407, 4548406, 4548403]   
16675_59777c66cfe0d44c58931d930161d282               [4547471, 4547452, 4547451, 4547435]   
16675_678811f2ba54a0ab8b1738e61bcf6ea1  [4551023, 4550988, 4550944, 4550824, 4550773, ...   
16675_6915f3003c0166f0c10040ce1b209cbb  [4548035, 4547794, 4547788, 4547786, 4547781, ...   
16675_747bd439aedc0cdd689f4c7de3fab5e9                        [4545119, 4545029, 4545028]   
16675_7fbb555e2f01e8a5fb217b69c8b4d13d  [4545618, 4544800, 4544443, 4544436, 4544430, ...   
16675_83ded8b269bd01e190091e82023ee368  [4545054, 4545038, 4545033, 4545032, 4545025, ...   
16675_88fd8e805b1365ee6b69fdbe321318dc                        [4542978, 4542945, 4542933]   
...                                                                                   ...   
17084_7240da86ee9252a28be57d41ebec5909  [5472, 5454, 5453, 5450, 5449, 5437, 5436, 543...   
17084_7ba66839c4c144c440e818847f39237f                           [3397, 3239, 3220, 3194]   
17084_7c981aba60c9c9f048d5f8cd783cf8c1  [9882, 9881, 9860, 9835, 9333, 7826, 7460, 730...   
17084_8909ef411a1092f71b7b57ae2bbeaff5                     [5254, 5253, 5252, 5163, 5140]   
17084_8bec5f6aa68e4e3e97a952df109c2fa6  [1539, 1133, 709, 483, 482, 476, 462, 397, 396...   
17084_8d6b3419f04fce98be2cc2c75bbf6288               [5013, 4996, 4995, 4963, 4961, 4905]   
17084_8dc67932e92851c26cb1ee1635e16839               [8409, 8381, 8379, 8285, 8128, 8117]   
17084_8e5747a512786708ae7838cdd5b073cd                     [5026, 4979, 4978, 4931, 4580]   
17084_90da53f519ced267c5da7bd92449fc03  [2773, 2341, 2096, 2073, 2071, 2070, 1890, 188...   
17084_91209a0fb34830e4c8e51017b014a557                           [9098, 9072, 9071, 8808]   
17084_93fcd779f1d1df6f9c79e4cb326cd753               [7456, 7437, 7435, 7434, 7423, 24

In [137]:
dff.revisit_intention.value_counts()

0    14916
1     8104
Name: revisit_intention, dtype: int64

In [139]:
a = [1, 2, 3, 4, 5]
a[:10]

[1, 2, 3, 4, 5]